In [19]:
import torch
import math


In [5]:
device = torch.device('cpu')

In [35]:
a=torch.randn((),device=device,dtype=torch.float64, requires_grad=True)
b=torch.randn((),device=device,dtype=torch.float64, requires_grad=True)
c=torch.randn((),device=device,dtype=torch.float64, requires_grad=True)
d=torch.randn((),device=device,dtype=torch.float64, requires_grad=True)

In [8]:
lr=1e-6

In [27]:
x = torch.linspace(-math.pi, math.pi, 2000, device=device)
y = torch.sin(x)
for t in range(20000):
    y_pred=a+b*x+c*x**2+d**3

    loss=(y_pred-y).pow(2).sum()
    if t%100==0:
        print(t, loss)
    loss.backward()

    with torch.no_grad():
        a-=lr*a.grad
        b-=lr*b.grad
        c-=lr*c.grad
        d-=lr*d.grad
        a.grad=torch.tensor(0,dtype=torch.float32)
        b.grad=torch.tensor(0,dtype=torch.float32)
        c.grad=torch.tensor(0,dtype=torch.float32)
        d.grad=torch.tensor(0,dtype=torch.float32)
    print(f'Result: y = {a.item()} + {b.item()} x + {c.item()} x^2 + {d.item()} x^3')

0 tensor(392.9561, grad_fn=<SumBackward0>)
Result: y = -0.0021025578025728464 + 0.3035065233707428 x + 0.002363398903980851 x^2 + -0.22630441188812256 x^3
Result: y = -0.0020789201371371746 + 0.3035065233707428 x + 0.0023592226207256317 x^2 + -0.22630077600479126 x^3
Result: y = -0.0020553243812173605 + 0.3035065233707428 x + 0.0023550535552203655 x^2 + -0.22629715502262115 x^3
Result: y = -0.0020317703019827604 + 0.3035065233707428 x + 0.00235089217312634 x^2 + -0.22629353404045105 x^3
Result: y = -0.0020082578994333744 + 0.3035065233707428 x + 0.002346737775951624 x^2 + -0.22628992795944214 x^3
Result: y = -0.0019847869407385588 + 0.3035065233707428 x + 0.0023425910621881485 x^2 + -0.22628632187843323 x^3
Result: y = -0.001961357658728957 + 0.3035065233707428 x + 0.002338451100513339 x^2 + -0.22628271579742432 x^3
Result: y = -0.0019379695877432823 + 0.3035065233707428 x + 0.00233431882224977 x^2 + -0.2262791246175766 x^3
Result: y = -0.001914622844196856 + 0.3035065233707428 x + 0.0

# PyTorch：定义新的 Autograd 函数
在幕后，每个原始的 Autograd 运算符实际上都是在张量上运行的两个函数。 正向函数从输入张量计算输出张量。 反向函数接收相对于某个标量值的输出张量的梯度，并计算相对于相同标量值的输入张量的梯度。

在 PyTorch 中，我们可以通过定义torch.autograd.Function的子类并实现forward和backward函数来轻松定义自己的 Autograd 运算符。 然后，我们可以通过构造实例并像调用函数一样调用新的 Autograd 运算符，并传递包含输入数据的张量。

在此示例中，我们将模型定义为y = a + b P[3](c + dx)而不是y = a + bx + cx ^ 2 + dx ^ 3，其中P[3](x) = 1/2 (5x ^ 3 - 3x)是三次的勒让德多项式。 我们编写了自己的自定义 Autograd 函数来计算P[3]的前进和后退，并使用它来实现我们的模型：

In [29]:
class LegendrePolynomial3(torch.autograd.Function):
    """
    We can implement our own custom autograd Functions by subclassing
    torch.autograd.Function and implementing the forward and backward passes
    which operate on Tensors.
    """
    @staticmethod
    def forward(ctx, input):
        """
        In the forward pass we receive a Tensor containing the input and return
        a Tensor containing the output. ctx is a context object that can be used
        to stash information for backward computation. You can cache arbitrary
        objects for use in the backward pass using the ctx.save_for_backward method.
        """
        ctx.save_for_backward(input)
        return 0.5 * (5 * input ** 3 - 3 * input)
    
    @staticmethod
    def backward(ctx, grad_output):
        """
        In the backward pass we receive a Tensor containing the gradient of the loss
        with respect to the output, and we need to compute the gradient of the loss
        with respect to the input.
        """
        input, = ctx.saved_tensors
        return grad_output * 1.5 * (5 * input ** 2 - 1)


# nn模块
PyTorch：nn
计算图和 Autograd 是定义复杂运算符并自动采用导数的非常强大的范例。 但是对于大型神经网络，原始的 Autograd 可能会太低级。

在构建神经网络时，我们经常想到将计算安排在层中，其中某些层具有可学习的参数，这些参数会在学习期间进行优化。

在 TensorFlow 中，像 Keras ， TensorFlow-Slim 和 TFLearn 之类的包在原始计算图上提供了更高层次的抽象，可用于构建神经网络。

在 PyTorch 中，nn包也达到了相同的目的。 nn包定义了一组模块，它们大致等效于神经网络层。 模块接收输入张量并计算输出张量，但也可以保持内部状态，例如包含可学习参数的张量。 nn包还定义了一组有用的损失函数，这些函数通常在训练神经网络时使用。

在此示例中，我们使用nn包来实现我们的多项式模型网络：

In [31]:
model = torch.nn.Sequential(
    torch.nn.Linear(3, 1),
    torch.nn.Flatten(0, 1)
)

In [32]:
loss_fn = torch.nn.MSELoss(reduction='sum')

In [36]:
lr = 1e-6
power = torch.tensor([1, 2, 3])
for t in range(20000):
    y_pred = model(x.unsqueeze(-1).pow(power))  # (2000,1)^(3,)=(2000,3)
    loss = loss_fn(y_pred, y)
    if t % 100 == 0:
        print(t, loss.item())
    model.zero_grad()
    loss.backward()
    with torch.no_grad():
        for param in model.parameters():
            param -= lr*param.grad
    linear_layer=model[0]
    print(f'Result: y = {linear_layer.bias.item()} + {linear_layer.weight[:, 0].item()} x + {linear_layer.weight[:, 1].item()} x^2 + {linear_layer.weight[:, 2].item()} x^3')

0 8.817168235778809
Result: y = 1.488906775648502e-08 + 0.8567266464233398 x + -1.21723537915841e-08 x^2 + -0.09332837164402008 x^3
Result: y = 1.4895475075604736e-08 + 0.8567266464233398 x + -1.2157094886333653e-08 x^2 + -0.09332837164402008 x^3
Result: y = 1.4901882394724453e-08 + 0.8567266464233398 x + -1.2141835981083204e-08 x^2 + -0.09332837164402008 x^3
Result: y = 1.4887726607071272e-08 + 0.8567266464233398 x + -1.2187612696834549e-08 x^2 + -0.09332837164402008 x^3
Result: y = 1.4895087829813747e-08 + 0.8567266464233398 x + -1.21723537915841e-08 x^2 + -0.09332837164402008 x^3
Result: y = 1.4901495148933463e-08 + 0.8567266464233398 x + -1.2157094886333653e-08 x^2 + -0.09332837164402008 x^3
Result: y = 1.4888769328536e-08 + 0.8567266464233398 x + -1.21723537915841e-08 x^2 + -0.09332837164402008 x^3
Result: y = 1.4895176647655717e-08 + 0.8567266464233398 x + -1.2157094886333653e-08 x^2 + -0.09332837164402008 x^3
Result: y = 1.4901583966775434e-08 + 0.8567266464233398 x + -1.2141835

# PyTorch：optim
到目前为止，我们已经通过使用torch.no_grad()手动更改持有可学习参数的张量来更新模型的权重。 对于像随机梯度下降这样的简单优化算法来说，这并不是一个巨大的负担，但是在实践中，我们经常使用更复杂的优化器（例如 AdaGrad，RMSProp，Adam 等）来训练神经网络。

PyTorch 中的optim包抽象了优化算法的思想，并提供了常用优化算法的实现。

在此示例中，我们将使用nn包像以前一样定义我们的模型，但是我们将使用optim包提供的 RMSprop 算法来优化模型：

In [37]:
optimizer = torch.optim.RMSprop(model.parameters(), lr=lr)

In [38]:
power = torch.tensor([1, 2, 3])
for t in range(20000):
    y_pred = model(x.unsqueeze(-1).pow(power))  # (2000,1)^(3,)=(2000,3)
    loss = loss_fn(y_pred, y)
    if t % 100 == 0:
        print(t, loss.item())
    optimizer.zero_grad()
    loss.backward()
    optimizer.step()
    print(f'Result: y = {linear_layer.bias.item()} + {linear_layer.weight[:, 0].item()} x + {linear_layer.weight[:, 1].item()} x^2 + {linear_layer.weight[:, 2].item()} x^3')

0 8.817168235778809
Result: y = 9.880864126898814e-06 + 0.8567366600036621 x + 9.922710887622088e-06 x^2 + -0.09333837032318115 x^3
Result: y = -1.1913107300642878e-07 + 0.8567466735839844 x + -7.728795026196167e-08 x^2 + -0.09332837164402008 x^3
Result: y = -3.126044845203069e-08 + 0.8567433953285217 x + 6.940986452264042e-09 x^2 + -0.09333153069019318 x^3
Result: y = -1.979989860956266e-08 + 0.8567441701889038 x + 1.3243139918017732e-08 x^2 + -0.09333065897226334 x^3
Result: y = -2.2573312108420396e-08 + 0.8567438721656799 x + 7.080425135086443e-09 x^2 + -0.09333088248968124 x^3
Result: y = -2.0382330490065215e-08 + 0.8567438721656799 x + 9.489109942251162e-09 x^2 + -0.09333080798387527 x^3
Result: y = -1.858948728283849e-08 + 0.8567437529563904 x + 1.0353688573161435e-08 x^2 + -0.09333081543445587 x^3
Result: y = -1.693551432424556e-08 + 0.8567436933517456 x + 1.096194246485993e-08 x^2 + -0.09333080053329468 x^3
Result: y = -1.5526996577364116e-08 + 0.8567436337471008 x + 1.11366045

# PyTorch：自定义nn模块
有时，您将需要指定比一系列现有模块更复杂的模型。 对于这些情况，您可以通过子类化nn.Module并定义一个forward来定义自己的模块，该模块使用其他模块或在 Tensors 上的其他自动转换操作来接收输入 Tensors 并生成输出 Tensors。

在此示例中，我们将三阶多项式实现为自定义Module子类：


In [40]:
class Polynomial3(torch.nn.Module):
    def __init__(self):
        super().__init__()
        self.a = torch.nn.Parameter(torch.randn(()))
        self.b = torch.nn.Parameter(torch.randn(()))
        self.c = torch.nn.Parameter(torch.randn(()))
        self.d = torch.nn.Parameter(torch.randn(()))

    def forward(self, x):
        return self.a + self.b * x + self.c*x**2 + self.d*x**3
    
    def __str__(self) -> str:
        return f'y = {self.a.item()} + {self.b.item()} x + {self.c.item()} x^2 + {self.d.item()} x^3'

In [42]:
x = torch.linspace(-math.pi, math.pi, 2000)
y = torch.sin(x)

# Construct our model by instantiating the class defined above
model = Polynomial3()

# Construct our loss function and an Optimizer. The call to model.parameters()
# in the SGD constructor will contain the learnable parameters of the nn.Linear
# module which is members of the model.
criterion = torch.nn.MSELoss(reduction='sum')
optimizer = torch.optim.SGD(model.parameters(), lr=1e-6)
for t in range(2000):
    # Forward pass: Compute predicted y by passing x to the model
    y_pred = model(x)

    # Compute and print loss
    loss = criterion(y_pred, y)
    if t % 100 == 99:
        print(t, loss.item())

    # Zero gradients, perform a backward pass, and update the weights.
    optimizer.zero_grad()
    loss.backward()
    optimizer.step()

print(f'Result: {model}')

99 2219.192138671875
199 1480.9586181640625
299 989.723388671875
399 662.7152099609375
499 444.9393005371094
599 299.84375
699 203.12745666503906
799 138.6273193359375
899 95.59001159667969
999 66.85800170898438
1099 47.665287017822266
1199 34.837181091308594
1299 26.257659912109375
1399 20.51576042175293
1499 16.670398712158203
1599 14.093289375305176
1699 12.364831924438477
1799 11.204715728759766
1899 10.425408363342285
1999 9.901483535766602
Result: y = 0.018876947462558746 + 0.8298319578170776 x + -0.003256586380302906 x^2 + -0.08950283378362656 x^3


In [56]:
class P(torch.nn.Module):
    def __init__(self):
        super().__init__()
        self.lin1 = torch.nn.Linear(784,10)

    def forward(self,x):
        x = self.lin1(x)
        return x


In [62]:
m = P()
print(m(torch.randn(784)))


tensor([-1.0216, -0.0277,  0.1261, -0.1084, -0.1733, -0.2156,  0.1313, -1.0768,
         0.6269, -0.3320], grad_fn=<AddBackward0>)


# 使用DataLoader重构
Pytorch 的DataLoader负责批量管理。 您可以从任何Dataset创建一个DataLoader。 DataLoader使迭代迭代变得更加容易。 不必使用train_ds[i*bs : i*bs+bs]，DataLoader会自动为我们提供每个小批量。

In [ ]:
from torch.utils.data import TensorDataset
from torch.utils.data import DataLoader

train_ds = TensorDataset(x_train, y_train)
train_dl = DataLoader(train_ds, batch_size=bs)
for xb,yb in train_dl:
    pred = model(xb)

对训练数据进行打乱对于防止批量与过拟合之间的相关性很重要。 另一方面，无论我们是否打乱验证集，验证损失都是相同的。 由于打乱需要花费更多时间，因此打乱验证数据没有任何意义。

我们将验证集的批量大小设为训练集的两倍。 这是因为验证集不需要反向传播，因此占用的内存更少（不需要存储梯度）。 我们利用这一优势来使用更大的批量，并更快地计算损失

In [ ]:
train_ds = TensorDataset(x_train, y_train)
train_dl = DataLoader(train_ds, batch_size=bs, shuffle=True)

valid_ds = TensorDataset(x_valid, y_valid)
valid_dl = DataLoader(valid_ds, batch_size=bs * 2)

（请注意，我们总是在训练之前调用**model.train()**，并在推理之前调用**model.eval()**，因为诸如**nn.BatchNorm2d**和**nn.Dropout**之类的层会使用它们，以确保这些不同阶段的行为正确。）